# <font color=red>DATA GATHERING I: MUSIC RELEASES AND THEIR GEOGRAPHICAL ORIGIN</font>

In this notebook, what we will do is identify the origin of each artist in Musicbrainz's database. Then, using the release table, we will associate each release with its author's origin.

For the releases whose origin hasn't been identified using Musicbrainz's database, we will use other sources to complete the missing values so that we have as many releases as possible.

In [114]:
import pandas as pd
import numpy as np
import time
import tqdm
import re
import warnings
import reverse_geocoder #pip install reverse geocoder in console
warnings.filterwarnings('ignore')

## <font color=blue>1) Artists' origin information</font>

### Data from Musicbrainz.org

In [115]:
#We open the table which contains all the artists:
artists= pd.read_csv('Data_in/Musicbrainz/artist.txt',sep='\t', header=None, engine='c', usecols=[0,1,3,11,17])
artists.columns = ['artist_id','artist_mbid','artist_name','start_area1', 'start_area2']
artists.head()

artist_id                           artist_mbid       artist_name  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1             WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Moutso, Pete   
2     273232  c112a400-af49-4665-8bba-741531d962a1           Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  Silhouettes, The   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Leavitt, Aric   

   start_area1  start_area2  
0          NaN          NaN  
1          NaN          NaN  
2          NaN          NaN  
3        222.0       7707.0  
4          NaN          NaN

In [116]:
#Let's see how many artists we have:
artists['artist_id'].nunique()

1476425

In [117]:
#How much info we have for each artist?
artists.notnull().sum(axis=0)

artist_id      1476425
artist_mbid    1476425
artist_name    1476414
start_area1     667983
start_area2     202424
dtype: int64

What are the "start_area1" and "start_area2"? If we look at Musicbrainz's field description for each artist (https://musicbrainz.org/doc/Artist), we can see that:

"Area: The artist area, as the name suggests, indicates the area with which an artist is primarily identified with. It is often, but not always, its birth/formation country."

We will keep this information as the artist's origin.

We need to incorporate as well the table called "artist credit", which gives us the artist credit_id. We will use this field to join later on each release with its artist:

In [118]:
artists_credit= pd.read_csv('Data_in/Musicbrainz/artist_credit_name.txt',\
                            sep='\t', header=None, engine='c', usecols=[0,2,3])
artists_credit.columns = ['credit_id','artist_id','artist_name']
artists_credit.head()

credit_id  artist_id             artist_name
0     578352     578352           Gustav Ruppke
1     273232     273232                 Zachary
2     153193     153193  The High Level Ranters
3      32262      32262        Georges Brassens
4    1389968    1171184    Harvard of the South

In [119]:
artists_credit.drop_duplicates(keep='first', inplace=True)

In [120]:
artists_credit.duplicated(subset='credit_id').value_counts()

False    1588033
True     1072366
dtype: int64

In [121]:
len(artists_credit)

2660399

In [122]:
#Let's join the artists with their credit id and verify that the matching is good:
df = pd.merge(artists_credit, artists, how='left', on='artist_id')
df.head()

credit_id  artist_id           artist_name_x  \
0     578352     578352           Gustav Ruppke   
1     273232     273232                 Zachary   
2     153193     153193  The High Level Ranters   
3      32262      32262        Georges Brassens   
4    1389968    1171184    Harvard of the South   

                            artist_mbid            artist_name_y  start_area1  \
0  b4f76788-7e6f-41b7-ac7b-dfb67f66282e           Ruppke, Gustav          NaN   
1  c112a400-af49-4665-8bba-741531d962a1                  Zachary          NaN   
2  c42eed94-e233-44e2-82b8-3ed6dd9bf318  High Level Ranters, The          NaN   
3  b58165ba-ac55-49a1-8855-caf16c68f5f2        Brassens, Georges         73.0   
4  bf8fefa4-c02d-4ad0-91d9-26f94169488f     Harvard of the South          NaN   

   start_area2  
0          NaN  
1          NaN  
2          NaN  
3      46130.0  
4          NaN

In [123]:
df.isnull().sum(axis=0)

credit_id              0
artist_id              0
artist_name_x         12
artist_mbid            0
artist_name_y         16
start_area1       884743
start_area2      1701200
dtype: int64

In [124]:
#We can now get rid of the duplicated artist_name column:
df.drop(labels=['artist_name_x'], axis=1, inplace=True)
df.head()

credit_id  artist_id                           artist_mbid  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318   
3      32262      32262  b58165ba-ac55-49a1-8855-caf16c68f5f2   
4    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f   

             artist_name_y  start_area1  start_area2  
0           Ruppke, Gustav          NaN          NaN  
1                  Zachary          NaN          NaN  
2  High Level Ranters, The          NaN          NaN  
3        Brassens, Georges         73.0      46130.0  
4     Harvard of the South          NaN          NaN

As we can see, the artist name and first name are separated by comma. In order to have a better formatting of the name, we will reverse the order of the names (ie: first name, family name) and remove the punctuation:

In [125]:
#A function to reverse the order of names:
def reverse(word):
    
    if ',' in word:
        b = word.split(',')
        rev = b[-1::-1]
        out = ' '.join(rev)
        return out
    
    else:
        return word

In [126]:
#We reverse the names in our dataframe:
df['artist_name'] = df['artist_name_y'].apply(lambda x: reverse(str(x)))
df.head()

credit_id  artist_id                           artist_mbid  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318   
3      32262      32262  b58165ba-ac55-49a1-8855-caf16c68f5f2   
4    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f   

             artist_name_y  start_area1  start_area2              artist_name  
0           Ruppke, Gustav          NaN          NaN            Gustav Ruppke  
1                  Zachary          NaN          NaN                  Zachary  
2  High Level Ranters, The          NaN          NaN   The High Level Ranters  
3        Brassens, Georges         73.0      46130.0         Georges Brassens  
4     Harvard of the South          NaN          NaN     Harvard of the South

In [127]:
#We remove the punctuation:
df['artist_name'] = df['artist_name'].apply(lambda x: re.sub(r"[^\w ]", " ", str(x), 0, re.MULTILINE))
df.head()

credit_id  artist_id                           artist_mbid  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318   
3      32262      32262  b58165ba-ac55-49a1-8855-caf16c68f5f2   
4    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f   

             artist_name_y  start_area1  start_area2              artist_name  
0           Ruppke, Gustav          NaN          NaN            Gustav Ruppke  
1                  Zachary          NaN          NaN                  Zachary  
2  High Level Ranters, The          NaN          NaN   The High Level Ranters  
3        Brassens, Georges         73.0      46130.0         Georges Brassens  
4     Harvard of the South          NaN          NaN     Harvard of the South

In [128]:
#We drop the non-formatted name column:
df.drop(labels=['artist_name_y'], axis=1, inplace=True)

We will try to retrieve, for each artist, the most detailed area we have, by using the subdivisions_all dataframe we generated in the notebook "Areas_Musicbrainz". That dataframe provides us with the coordinates for each area_id that is not a country.

In [129]:
areas = pd.read_csv('Data_in/Musicbrainz/area.txt',sep='\t', header=None, engine='python', usecols=[0,2,3])
areas.columns = ['area_id','area_name','code_type']
areas.head()

area_id area_name  code_type
0    15449   Greccio        4.0
1       38    Canada        1.0
2       43     Chile        1.0
3       44     China        1.0
4       36  Cambodia        1.0

In [130]:
sub_coordinates = pd.read_csv('Data_out/subdivisions_all.csv', sep='\t', header=0, encoding='utf-8')
sub_coordinates.head()

area_id area_name subdivision_name   country_name   latitude   longitude
0      262       NaN           Alaska  United States  64.200841 -149.493673
1      339       NaN   Sachsen-Anhalt        Germany  51.950265   11.692273
2      263       NaN          Alabama  United States  32.318231  -86.902298
3      261       NaN         Maryland  United States  39.045755  -76.641271
4      264       NaN         Arkansas  United States  35.201050  -91.831833

In [131]:
#We merge both dataframes, to have all our area_id's (countries and other subdivisions that we couldn't retrieve in
#the previous notebook won't have coordinates in this dataframe):
areas_coordinates = pd.merge(areas, sub_coordinates, how='left', on='area_id')
areas_coordinates.head()

area_id area_name_x  code_type area_name_y subdivision_name country_name  \
0    15449     Greccio        4.0     Greccio            Lazio        Italy   
1       38      Canada        1.0         NaN              NaN          NaN   
2       43       Chile        1.0         NaN              NaN          NaN   
3       44       China        1.0         NaN              NaN          NaN   
4       36    Cambodia        1.0         NaN              NaN          NaN   

    latitude  longitude  
0  41.655242  12.989615  
1        NaN        NaN  
2        NaN        NaN  
3        NaN        NaN  
4        NaN        NaN

In [132]:
len(areas_coordinates)

117674

In [133]:
areas_coordinates.duplicated(subset='area_id').any()

False

#### Selecting the origin for each artist credit:

1) Merging by start_area1:

In [134]:
df1 = pd.merge(df, areas_coordinates, how='left', left_on='start_area1', right_on='area_id')
df1.head()

credit_id  artist_id                           artist_mbid  start_area1  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e          NaN   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1          NaN   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318          NaN   
3      32262      32262  b58165ba-ac55-49a1-8855-caf16c68f5f2         73.0   
4    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f          NaN   

   start_area2              artist_name  area_id area_name_x  code_type  \
0          NaN            Gustav Ruppke      NaN         NaN        NaN   
1          NaN                  Zachary      NaN         NaN        NaN   
2          NaN   The High Level Ranters      NaN         NaN        NaN   
3      46130.0         Georges Brassens     73.0      France        1.0   
4          NaN     Harvard of the South      NaN         NaN        NaN   

  area_name_y subdivision_name country_name  latitude  longitude  
0         NaN              NaN          NaN       NaN        NaN  
1         NaN              NaN          NaN       NaN        NaN  
2         NaN              NaN          NaN       NaN        NaN  
3         NaN              NaN          NaN       NaN        NaN  
4         NaN              NaN          NaN       NaN        NaN

In [135]:
#How many coordinates do we have for each artist credit?
df1.notnull().sum(axis=0)

credit_id           2660399
artist_id           2660399
artist_mbid         2660399
start_area1         1775656
start_area2          959199
artist_name         2660399
area_id             1775656
area_name_x         1775656
code_type           1772441
area_name_y          163348
subdivision_name     268749
country_name         268749
latitude             268749
longitude            268749
dtype: int64

In [136]:
len(df1)

2660399

In [137]:
#We save the retrieved credit areas:
retrieved_credit1 = df1[df1['country_name'].notnull()]
len(retrieved_credit1)

268749

In [138]:
pending_credit1 = df1[df1['country_name'].isnull()]
#drop empty columns:
to_drop = ['area_id', 'area_name_x', 'code_type', 'area_name_y', 'country_name', 'latitude', 'longitude']
pending_credit1.drop(labels=to_drop, axis=1, inplace=True)

In [139]:
pending_credit1.head()

credit_id  artist_id                           artist_mbid  start_area1  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e          NaN   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1          NaN   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318          NaN   
3      32262      32262  b58165ba-ac55-49a1-8855-caf16c68f5f2         73.0   
4    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f          NaN   

   start_area2              artist_name subdivision_name  
0          NaN            Gustav Ruppke              NaN  
1          NaN                  Zachary              NaN  
2          NaN   The High Level Ranters              NaN  
3      46130.0         Georges Brassens              NaN  
4          NaN     Harvard of the South              NaN

2) Merging by start_area2:

In [140]:
df2 = pd.merge(pending_credit1, areas_coordinates, how='left', left_on='start_area2', right_on='area_id')
df2.head()

credit_id  artist_id                           artist_mbid  start_area1  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e          NaN   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1          NaN   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318          NaN   
3      32262      32262  b58165ba-ac55-49a1-8855-caf16c68f5f2         73.0   
4    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f          NaN   

   start_area2              artist_name subdivision_name_x  area_id  \
0          NaN            Gustav Ruppke                NaN      NaN   
1          NaN                  Zachary                NaN      NaN   
2          NaN   The High Level Ranters                NaN      NaN   
3      46130.0         Georges Brassens                NaN  46130.0   
4          NaN     Harvard of the South                NaN      NaN   

  area_name_x  code_type area_name_y subdivision_name_y country_name  \
0         NaN        NaN         NaN                NaN          NaN   
1         NaN        NaN         NaN                NaN          NaN   
2         NaN        NaN         NaN                NaN          NaN   
3        Sète        3.0        Sète          Occitanie       France   
4         NaN        NaN         NaN                NaN          NaN   

    latitude  longitude  
0        NaN        NaN  
1        NaN        NaN  
2        NaN        NaN  
3  43.892723   3.282763  
4        NaN        NaN

In [141]:
#How many coordinates do we have for each artist credit in this second merge?
df2.notnull().sum(axis=0)

credit_id             2391650
artist_id             2391650
artist_mbid           2391650
start_area1           1506907
start_area2            840900
artist_name           2391650
subdivision_name_x          0
area_id                840900
area_name_x            840900
code_type              840742
area_name_y            685321
subdivision_name_y     805681
country_name           805681
latitude               805681
longitude              805681
dtype: int64

In [142]:
retrieved_credit2 = df2[df2['country_name'].notnull()]

In [143]:
pending_credit2 = df2[df2['country_name'].isnull()]
#drop empty columns:
to_drop = ['area_id', 'area_name_x', 'code_type', 'area_name_y', 'country_name', 'latitude', 'longitude']
pending_credit2.drop(labels=to_drop, axis=1, inplace=True)

In [144]:
pending_credit2.head()

credit_id  artist_id                           artist_mbid  start_area1  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e          NaN   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1          NaN   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318          NaN   
4    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f          NaN   
5     145773     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c          NaN   

   start_area2              artist_name subdivision_name_x subdivision_name_y  
0          NaN            Gustav Ruppke                NaN                NaN  
1          NaN                  Zachary                NaN                NaN  
2          NaN   The High Level Ranters                NaN                NaN  
4          NaN     Harvard of the South                NaN                NaN  
5          NaN             Aric Leavitt                NaN                NaN

### Data from the 1 million songs dataset

Between 2011 and 2012, there was a Music Information Retrieval challenge called "Million Song Dataset". The majority of the data contained was provided by The Echo Nest (today known as Spotify).

At the bottom of the following website, there are links to download the Dataset:

https://labrosa.ee.columbia.edu/millionsong/pages/getting-dataset

As we won't use the whole dataset (just some of the tables), you don't need to download them: they will be attached in the repo.

What we will do now is try to identify the origin for the pending_credit2 dataframe using this new data source:

In [145]:
artists_locations = pd.read_csv('Data_in/1M_songs/artist_location.csv',sep='<SEP>', header=None, engine='python')
artists_locations.columns = ['artist_id','lat','long','artist_name','location_name']
artists_locations.head()

artist_id       lat      long           artist_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804          Endless Blue   
1  AR8K6F31187B99C2BC  46.44231 -93.36586               Go Fish   
2  ARHJJ771187FB5B581  51.59678  -0.33556  Screaming Lord Sutch   
3  ARJ8YLL1187FB3CA93  40.69626 -73.83301          Morton Gould   
4  ARYBAGV11ECC836DAC  43.58828 -79.64372        Crash Parallel   

                location_name  
0                  Santa Cruz  
1             Twin Cities, MN  
2  Harrow, Middlesex, England  
3           Richmond Hill, NY  
4                 Mississauga

In [146]:
#How many artist are there?
artists_locations['artist_id'].nunique()

13850

In this dataset, there is also another table which provides us with some extra information, especially the artist Musicbrainz's id (which will be very helpful to link with Musicbrainz's dataframe).

In [147]:
metadata = pd.read_csv('Data_in/1M_songs/track_metadata.csv',sep=',', header=0,\
                       engine='python', usecols=['artist_id','artist_mbid'])
metadata.head()

artist_id                           artist_mbid
0  ARYZTJS1187B98C555  357ff05d-848a-44cf-b608-cb34b5701ae5
1  ARMVN3U1187FB3A1EB  8d7ef530-a6fd-4f8f-b2e2-74aec765e0f9
2  ARGEKB01187FB50750  3d403d44-36ce-465c-ad43-ae877e65adc4
3  ARNWYLR1187B9B2F9C  12be7648-7094-495f-90e6-df4189d68615
4  AREQDTE1269FB37231                                   NaN

In [148]:
#We drop the rows without artist_mbid (as we can't link them with our df)
metadata.dropna(subset=['artist_mbid'],axis=0, inplace=True)
#We merge artist_locations and metadata dataframes:
merged = pd.merge(artists_locations,metadata,how='left',on='artist_id')
merged.dropna(subset=['artist_mbid'],axis=0, inplace=True)
merged.head()

artist_id       lat      long   artist_name    location_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
1  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
2  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
3  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
4  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   

                            artist_mbid  
0  0bd9755c-c86d-431c-bc28-ef908b8a9821  
1  0bd9755c-c86d-431c-bc28-ef908b8a9821  
2  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
3  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
4  d4620364-82ec-4c34-9265-a2b72dfa8e3e

In [149]:
#We delete the useless columns:
merged.drop(labels=['artist_id','artist_name'], axis=1, inplace=True)
#We get rid of the duplicate rows:
merged.drop_duplicates(subset='artist_mbid', inplace=True)
merged.head()

lat      long               location_name  \
0  -16.96595 -61.14804                  Santa Cruz   
2   46.44231 -93.36586             Twin Cities, MN   
33  51.59678  -0.33556  Harrow, Middlesex, England   
64  40.69626 -73.83301           Richmond Hill, NY   
78  43.58828 -79.64372                 Mississauga   

                             artist_mbid  
0   0bd9755c-c86d-431c-bc28-ef908b8a9821  
2   d4620364-82ec-4c34-9265-a2b72dfa8e3e  
33  e1079a78-75d4-4a1a-aef1-0be051386598  
64  4db4e744-3007-4386-b87d-9653acfe0464  
78  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8

As we can see above, even if we have the coordinates, we would still like to get the country name and the subdivision.

Before starting to retrieve geographical information about these artists, we will identify the ones that are actually pending (ie: not in our retrieved_credit dataframes):

In [150]:
list1 = retrieved_credit1.artist_mbid.values.tolist()
list2 = retrieved_credit2.artist_mbid.values.tolist()
final_list = list1 + list2

In [151]:
to_retrieve = merged[~merged.artist_mbid.isin(final_list)]
len(to_retrieve)

5819

In [152]:
to_retrieve.head()

lat      long     location_name  \
0   -16.96595 -61.14804        Santa Cruz   
2    46.44231 -93.36586   Twin Cities, MN   
78   43.58828 -79.64372       Mississauga   
89   59.91228  10.74998              Oslo   
221  38.89910 -77.02900  Washington, D.C.   

                              artist_mbid  
0    0bd9755c-c86d-431c-bc28-ef908b8a9821  
2    d4620364-82ec-4c34-9265-a2b72dfa8e3e  
78   b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8  
89   276f08c2-4b4b-4e45-bab8-3ebe6066e080  
221  9320918d-5143-4846-bab8-7ad48ec17d58

Using the coordinates and the reverse_geocoder tool, we can proceed to retrieve the info we need:

In [153]:
#We first create a new column called "coords" in which we'll gather both latitude and longitude:
to_retrieve['coords'] = list(zip(to_retrieve.lat, to_retrieve.long))
coords = tuple(to_retrieve['coords'].values.tolist())
#And now we use the reverse_geocoder utility to retrieve info for each pair of coordinates:
address = reverse_geocoder.search(coords)
to_retrieve['address'] = address
to_retrieve.head()

lat      long     location_name  \
0   -16.96595 -61.14804        Santa Cruz   
2    46.44231 -93.36586   Twin Cities, MN   
78   43.58828 -79.64372       Mississauga   
89   59.91228  10.74998              Oslo   
221  38.89910 -77.02900  Washington, D.C.   

                              artist_mbid                  coords  \
0    0bd9755c-c86d-431c-bc28-ef908b8a9821  (-16.96595, -61.14804)   
2    d4620364-82ec-4c34-9265-a2b72dfa8e3e   (46.44231, -93.36586)   
78   b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8   (43.58828, -79.64372)   
89   276f08c2-4b4b-4e45-bab8-3ebe6066e080    (59.91228, 10.74998)   
221  9320918d-5143-4846-bab8-7ad48ec17d58      (38.8991, -77.029)   

                                               address  
0    {'lat': '-16.43333', 'lon': '-60.9', 'name': '...  
2    {'lat': '46.53301', 'lon': '-93.71025', 'name'...  
78   {'lat': '43.5789', 'lon': '-79.6583', 'name': ...  
89   {'lat': '59.91273', 'lon': '10.74609', 'name':...  
221  {'lat': '38.89511', 'lon': '-77.03637', 'name'...

In [154]:
#Let's see how this new info is formatted:
to_retrieve['address'][0]

OrderedDict([('lat', '-16.43333'),
             ('lon', '-60.9'),
             ('name', 'Concepcion'),
             ('admin1', 'Santa Cruz'),
             ('admin2', ''),
             ('cc', 'BO')])

What we want to retrieve is the country ("cc" in ISO format), the admin1 (subdivision) and the name of the location:

In [155]:
#Resetting index for the following step:
to_retrieve.reset_index(drop=True, inplace=True)

In [156]:
#First, the ISO code of the country:
to_retrieve['ISO_code'] = [list(to_retrieve['address'][row].items())[5][1]\
                           for row in range(len(to_retrieve))]

In [157]:
#Then, the area_name:
to_retrieve['area_name'] = [list(to_retrieve['address'][row].items())[2][1]\
                            for row in range(len(to_retrieve))]

In [158]:
#And finally, the subdivision:
to_retrieve['subdivision_name'] = [list(to_retrieve['address'][row].items())[3][1]\
                                   for row in range(len(to_retrieve))]

In [159]:
to_retrieve.head()

lat      long     location_name                           artist_mbid  \
0 -16.96595 -61.14804        Santa Cruz  0bd9755c-c86d-431c-bc28-ef908b8a9821   
1  46.44231 -93.36586   Twin Cities, MN  d4620364-82ec-4c34-9265-a2b72dfa8e3e   
2  43.58828 -79.64372       Mississauga  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8   
3  59.91228  10.74998              Oslo  276f08c2-4b4b-4e45-bab8-3ebe6066e080   
4  38.89910 -77.02900  Washington, D.C.  9320918d-5143-4846-bab8-7ad48ec17d58   

                   coords                                            address  \
0  (-16.96595, -61.14804)  {'lat': '-16.43333', 'lon': '-60.9', 'name': '...   
1   (46.44231, -93.36586)  {'lat': '46.53301', 'lon': '-93.71025', 'name'...   
2   (43.58828, -79.64372)  {'lat': '43.5789', 'lon': '-79.6583', 'name': ...   
3    (59.91228, 10.74998)  {'lat': '59.91273', 'lon': '10.74609', 'name':...   
4      (38.8991, -77.029)  {'lat': '38.89511', 'lon': '-77.03637', 'name'...   

  ISO_code         area_name  subdivision_name  
0       BO        Concepcion        Santa Cruz  
1       US            Aitkin         Minnesota  
2       CA       Mississauga           Ontario  
3       NO              Oslo              Oslo  
4       US  Washington, D.C.  Washington, D.C.

Now, what we want is to identify the country name via its ISO code. Thankfully, Musicbrainz also has a table which contains that information:

In [160]:
#We load the ISO table:
ISO1 = pd.read_csv('Data_in/Musicbrainz/iso_3166_1.txt',sep='\t', header=None, engine='python')
ISO1.columns = ['area_id','ISO_code']
ISO1.head()

area_id ISO_code
0        1       AF
1        2       AL
2        3       DZ
3        4       AS
4        5       AD

In [161]:
#Retrieving the country name via Musicbrainz's ISO codes and areas:
areas_countries = pd.read_csv('Data_in/Musicbrainz/area.txt',\
                              sep='\t', header=None, engine='python', usecols=[0,2,3])
areas_countries.columns = ['area_id','area_name','code_type']

In [162]:
#Let's see the area types we have:
area_types = pd.read_csv('Data_in/Musicbrainz/area_type.txt',\
                         sep='\t', header=None, engine='python', usecols=[1,3,4])
area_types.columns = ['type','code_type','definition']
area_types.head()

type  code_type                                         definition
0       Country          1  Country is used for areas included (or previou...
1   Subdivision          2  Subdivision is used for the main administrativ...
2        County          7  County is used for smaller administrative divi...
3  Municipality          4  Municipality is used for small administrative ...
4          City          3  City is used for settlements of any size, incl...

We need to keep only the countries, so code_type equal to 1:

In [163]:
countries = areas_countries[areas_countries['code_type'] ==1]
countries.head()

area_id area_name  code_type
1       38    Canada        1.0
2       43     Chile        1.0
3       44     China        1.0
4       36  Cambodia        1.0
5       78     Gabon        1.0

In [164]:
#We combine both dataframes:
countries_ISO = pd.merge(countries, ISO1, how='left', on='area_id')
countries_ISO.head()

area_id area_name  code_type ISO_code
0       38    Canada        1.0       CA
1       43     Chile        1.0       CL
2       44     China        1.0       CN
3       36  Cambodia        1.0       KH
4       78     Gabon        1.0       GA

In [165]:
#As they are countries, we change the column name to country:
countries_ISO.rename(columns={'area_name':'country_name'}, inplace=True)
#And drop the rest of the columns before merging:
countries_ISO.drop(labels=['area_id', 'code_type'], axis=1, inplace=True)

In [166]:
#And now we can merge the country name into our "to_retrieve" dataframe:
retrieved_artist = pd.merge(to_retrieve, countries_ISO, how='left', on='ISO_code')
retrieved_artist.head()

lat      long     location_name                           artist_mbid  \
0 -16.96595 -61.14804        Santa Cruz  0bd9755c-c86d-431c-bc28-ef908b8a9821   
1  46.44231 -93.36586   Twin Cities, MN  d4620364-82ec-4c34-9265-a2b72dfa8e3e   
2  43.58828 -79.64372       Mississauga  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8   
3  59.91228  10.74998              Oslo  276f08c2-4b4b-4e45-bab8-3ebe6066e080   
4  38.89910 -77.02900  Washington, D.C.  9320918d-5143-4846-bab8-7ad48ec17d58   

                   coords                                            address  \
0  (-16.96595, -61.14804)  {'lat': '-16.43333', 'lon': '-60.9', 'name': '...   
1   (46.44231, -93.36586)  {'lat': '46.53301', 'lon': '-93.71025', 'name'...   
2   (43.58828, -79.64372)  {'lat': '43.5789', 'lon': '-79.6583', 'name': ...   
3    (59.91228, 10.74998)  {'lat': '59.91273', 'lon': '10.74609', 'name':...   
4      (38.8991, -77.029)  {'lat': '38.89511', 'lon': '-77.03637', 'name'...   

  ISO_code         area_name  subdivision_name   country_name  
0       BO        Concepcion        Santa Cruz        Bolivia  
1       US            Aitkin         Minnesota  United States  
2       CA       Mississauga           Ontario         Canada  
3       NO              Oslo              Oslo         Norway  
4       US  Washington, D.C.  Washington, D.C.  United States

In [167]:
#Did we miss any country?
retrieved_artist.isnull().sum(axis=0)

lat                 0
long                0
location_name       3
artist_mbid         0
coords              0
address             0
ISO_code            0
area_name           0
subdivision_name    0
country_name        6
dtype: int64

In [168]:
retrieved_artist[retrieved_artist.country_name.isnull()]

lat        long location_name  \
649   25.026980  121.497130           108   
1008 -22.965660   18.486170       Detroit   
2692  24.206660  120.851530      Taichung   
3306  23.599751  121.023811        Taiwan   
4426  25.026980  121.497130           108   
5081  23.599750  121.023810        Taiwan   

                               artist_mbid                           coords  \
649   4fdd526e-3c9f-43d2-aef6-d8bf7dbe4fd8            (25.02698, 121.49713)   
1008  3c34ad84-7628-459e-949d-c27e2ae73231            (-22.96566, 18.48617)   
2692  4a965b5a-1177-4ead-a2a8-932d6f12e734   (24.20666, 120.85153000000001)   
3306  300db63b-7614-4642-b306-400c6b54bb20  (23.599751, 121.02381100000001)   
4426  7332456e-c76e-4362-ad31-d84fd34a4942            (25.02698, 121.49713)   
5081  90c879b6-b4d1-4632-b66a-cdd4ed766cde   (23.59975, 121.02381000000001)   

                                                address ISO_code area_name  \
649   {'lat': '25.01427', 'lon': '121.46719', 'name'...       TW   Banqiao   
1008  {'lat': '-22.45', 'lon': '18.96667', 'name': '...       NA   Gobabis   
2692  {'lat': '24.25', 'lon': '120.71694', 'name': '...       TW  Fengyuan   
3306  {'lat': '23.74639', 'lon': '120.7525', 'name':...       TW      Lugu   
4426  {'lat': '25.01427', 'lon': '121.46719', 'name'...       TW   Banqiao   
5081  {'lat': '23.74639', 'lon': '120.7525', 'name':...       TW      Lugu   

     subdivision_name country_name  
649            Taipei          NaN  
1008          Omaheke          NaN  
2692           Taiwan          NaN  
3306           Taiwan          NaN  
4426           Taipei          NaN  
5081           Taiwan          NaN

The file didn't recognize the country codes TW and NA, so we'll input this information manually (please note that Taiwan belongs to China, and NA reffers to Namibia):

In [169]:
for i in [649, 2692, 3306, 4426, 5081]:
    retrieved_artist['country_name'][i] = 'China'
    
retrieved_artist['country_name'][1008] = 'Namibia'

In [170]:
retrieved_artist.head()

lat      long     location_name                           artist_mbid  \
0 -16.96595 -61.14804        Santa Cruz  0bd9755c-c86d-431c-bc28-ef908b8a9821   
1  46.44231 -93.36586   Twin Cities, MN  d4620364-82ec-4c34-9265-a2b72dfa8e3e   
2  43.58828 -79.64372       Mississauga  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8   
3  59.91228  10.74998              Oslo  276f08c2-4b4b-4e45-bab8-3ebe6066e080   
4  38.89910 -77.02900  Washington, D.C.  9320918d-5143-4846-bab8-7ad48ec17d58   

                   coords                                            address  \
0  (-16.96595, -61.14804)  {'lat': '-16.43333', 'lon': '-60.9', 'name': '...   
1   (46.44231, -93.36586)  {'lat': '46.53301', 'lon': '-93.71025', 'name'...   
2   (43.58828, -79.64372)  {'lat': '43.5789', 'lon': '-79.6583', 'name': ...   
3    (59.91228, 10.74998)  {'lat': '59.91273', 'lon': '10.74609', 'name':...   
4      (38.8991, -77.029)  {'lat': '38.89511', 'lon': '-77.03637', 'name'...   

  ISO_code         area_name  subdivision_name   country_name  
0       BO        Concepcion        Santa Cruz        Bolivia  
1       US            Aitkin         Minnesota  United States  
2       CA       Mississauga           Ontario         Canada  
3       NO              Oslo              Oslo         Norway  
4       US  Washington, D.C.  Washington, D.C.  United States

In [171]:
#Dropping unnecessary columns before merging with our pending dataframe:
to_drop = ['location_name','coords', 'address', 'ISO_code']
retrieved_artist.drop(labels=to_drop, axis=1, inplace=True)
#Renaming columns:
retrieved_artist.rename(columns={'lat':'latitude','long':'longitude'}, inplace=True)

In [172]:
#And now we cand merge it with our pending2 dataframe:
df3 = pd.merge(pending_credit2, retrieved_artist, how='left', on='artist_mbid')
df3.head()

credit_id  artist_id                           artist_mbid  start_area1  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e          NaN   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1          NaN   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318          NaN   
3    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f          NaN   
4     145773     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c          NaN   

   start_area2              artist_name subdivision_name_x subdivision_name_y  \
0          NaN            Gustav Ruppke                NaN                NaN   
1          NaN                  Zachary                NaN                NaN   
2          NaN   The High Level Ranters                NaN                NaN   
3          NaN     Harvard of the South                NaN                NaN   
4          NaN             Aric Leavitt                NaN                NaN   

   latitude  longitude area_name subdivision_name country_name  
0       NaN        NaN       NaN              NaN          NaN  
1       NaN        NaN       NaN              NaN          NaN  
2       NaN        NaN       NaN              NaN          NaN  
3       NaN        NaN       NaN              NaN          NaN  
4       NaN        NaN       NaN              NaN          NaN

In [173]:
#How many coordinates do we have for each artist credit in this third merge?
df3.notnull().sum(axis=0)

credit_id             1585979
artist_id             1585979
artist_mbid           1585979
start_area1            719494
start_area2             35219
artist_name           1585979
subdivision_name_x          0
subdivision_name_y          0
latitude                29666
longitude               29666
area_name               29666
subdivision_name        29666
country_name            29666
dtype: int64

Thanks to the 1 Million Songs Dataset, we have been able to retrieve the origin for 29.666 artist credits.

We'll save it in retrieved_credit3 and see what's pending:

In [174]:
#We first drop the duplicated subdivision columns:
df3.drop(labels=['subdivision_name_x', 'subdivision_name_y'], axis=1, inplace=True)
#And save the retrieved ones:
retrieved_credit3 = df3[df3['country_name'].notnull()]

In [175]:
pending_credit3 = df3[df3['country_name'].isnull()]
#drop empty columns:
to_drop = ['subdivision_name', 'area_name', 'country_name', 'latitude', 'longitude']
pending_credit3.drop(labels=to_drop, axis=1, inplace=True)

In [176]:
#How many artists do we have without origin information?
pending_credit3['artist_id'].nunique()

809640

### Data from Wikidata Query with SPARQL

Wikidata has an online query service (https://query.wikidata.org/) which we will use to retrieve the pending artists' origin. 

I ran the following 3 queries and saved the results in Data_in/wikidata:

1) Musicians

SELECT ?musician ?musicianLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?place_of_birth ?place_of_birthLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?musician wdt:P106 wd:Q639669.
  OPTIONAL { ?musician wdt:P136 ?genre. }
  OPTIONAL { ?musician wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?musician wdt:P19 ?place_of_birth. }
}


--> Export to csv file: query_wikidata_musicians.csv

2) Singers

SELECT ?musician ?musicianLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?place_of_birth ?place_of_birthLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?musician wdt:P106 wd:Q177220.
  OPTIONAL { ?musician wdt:P136 ?genre. }
  OPTIONAL { ?musician wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?musician wdt:P19 ?place_of_birth. }
}

--> Export to csv file: query_wikidata_singers.csv

3) Bands

SELECT ?band ?bandLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?location_of_formation ?location_of_formationLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?band wdt:P31 wd:Q215380.
  OPTIONAL { ?band wdt:P136 ?genre. }
  OPTIONAL { ?band wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?band wdt:P740 ?location_of_formation. }
}

--> Export to csv file: query_wikidata_bands.csv

In [177]:
#Open the files and load them into dataframes with the same column names (to match with our main dataframe later):
musicians = pd.read_csv('Data_in/wikidata/query_wikidata_musicians.csv',\
                        sep=',', encoding='utf-8', usecols=[4,6])
musicians.rename(columns={'MusicBrainz_artist_ID':'artist_mbid',\
                          'place_of_birthLabel':'area_name'}, inplace=True)

In [178]:
#Singers:
singers = pd.read_csv('Data_in/wikidata/query_wikidata_singers.csv',\
                      sep=',', encoding='utf-8', usecols=[4,6])
singers.rename(columns={'MusicBrainz_artist_ID':'artist_mbid',\
                        'place_of_birthLabel':'area_name'}, inplace=True)

In [179]:
#Bands:
bands = pd.read_csv('Data_in/wikidata/query_wikidata_bands.csv',\
                    sep=',', encoding='utf-8', usecols=[4,6])
bands.rename(columns={'MusicBrainz_artist_ID':'artist_mbid',\
                      'location_of_formationLabel':'area_name'}, inplace=True)

In [180]:
bands.head()

artist_mbid   area_name
0  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
1  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
2  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
3  a3cb23fc-acd3-4ce0-8f36-1e5aa6a18432      Dublin
4  a3cb23fc-acd3-4ce0-8f36-1e5aa6a18432      Dublin

In [181]:
#Now we can concatenate the 3 dataframes into one:
wiki_df = pd.concat([musicians, singers, bands])
wiki_df.head()

artist_mbid              area_name
0                                   NaN  Cherbourg-en-Cotentin
1  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
2  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
3  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
4  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg

In [182]:
#We can directly drop the rows which don't have a musicbrainz's id (we need and ID to join with our main df):
wiki_df.dropna(subset=['artist_mbid'], axis=0, inplace=True)

In [183]:
len(wiki_df)

116020

In [184]:
#Let's see how many artists we have:
wiki_df['artist_mbid'].nunique()

96110

In [185]:
#Drop duplicated artist_mbid:
wiki_df.drop_duplicates(subset=['artist_mbid'],keep='first', inplace=True)

In [186]:
#What kind of information do we have in the column origin_name?:
wiki_df.area_name.value_counts()

New York City                               1273
Los Angeles                                 1209
London                                       995
Tokyo                                        750
Paris                                        440
Chicago                                      436
Brooklyn                                     390
Seoul                                        376
Philadelphia                                 348
Toronto                                      333
Berlin                                       324
Stockholm                                    323
San Francisco                                289
Seattle                                      282
Boston                                       268
Moscow                                       267
California                                   266
Montreal                                     248
Detroit                                      248
Oslo                                         219
Rome                

It looks like we have city names, so we can use our sub_coordinates dataframe to match by area_name. However, we'll have to drop duplicates in both retrieved areas and wiki_df, to avoid mismatching.

In [187]:
#We first delete the duplicate area names in our wiki_df:
wiki_df.drop_duplicates(subset='area_name', keep=False, inplace=True)
#We do the same with our retrieved_areas dataframe:
areas_dedup = sub_coordinates.drop_duplicates(subset='area_name', keep=False)

In [188]:
#Now we can merge wiki_df with areas_dedup:
retrieved_wiki = pd.merge(wiki_df, areas_dedup, how='left', on='area_name')
retrieved_wiki.head()

artist_mbid      area_name   area_id  \
0  4b585938-f271-45e2-b19a-91c634b5e396    Bexleyheath       NaN   
1  dc0640db-f5db-4fde-a5ca-ab1331f94a43       Anchiano       NaN   
2  6fdd3b3e-1ea6-4da9-8d6f-8f8de01c133a        Ciboure   49448.0   
3  09ff1fe8-d61c-4b98-bb82-18487c74d7b7  Żelazowa Wola   88730.0   
4  2a33d974-ad9e-4b51-917e-fb9397bf82c6    Puente Alto  115951.0   

                   subdivision_name country_name   latitude  longitude  
0                               NaN          NaN        NaN        NaN  
1                               NaN          NaN        NaN        NaN  
2                Nouvelle-Aquitaine       France  45.708718   0.626891  
3                       Mazowieckie       Poland  51.892718  21.002168  
4  Región Metropolitana de Santiago        Chile -33.437554 -70.650490

In [189]:
retrieved_wiki.country_name.isnull().value_counts()

False    3598
True     3584
Name: country_name, dtype: int64

In [190]:
#Before the merging, we drop the rows we didn't identify:
retrieved_wiki.dropna(subset=['country_name'], axis=0, inplace=True)

In [191]:
#And now we cand merge it with our pending3 dataframe:
df4 = pd.merge(pending_credit3, retrieved_wiki, how='left', on='artist_mbid')
df4.head()

credit_id  artist_id                           artist_mbid  start_area1  \
0     578352     578352  b4f76788-7e6f-41b7-ac7b-dfb67f66282e          NaN   
1     273232     273232  c112a400-af49-4665-8bba-741531d962a1          NaN   
2     153193     153193  c42eed94-e233-44e2-82b8-3ed6dd9bf318          NaN   
3    1389968    1171184  bf8fefa4-c02d-4ad0-91d9-26f94169488f          NaN   
4     145773     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c          NaN   

   start_area2              artist_name area_name  area_id subdivision_name  \
0          NaN            Gustav Ruppke       NaN      NaN              NaN   
1          NaN                  Zachary       NaN      NaN              NaN   
2          NaN   The High Level Ranters       NaN      NaN              NaN   
3          NaN     Harvard of the South       NaN      NaN              NaN   
4          NaN             Aric Leavitt       NaN      NaN              NaN   

  country_name  latitude  longitude  
0          NaN       NaN        NaN  
1          NaN       NaN        NaN  
2          NaN       NaN        NaN  
3          NaN       NaN        NaN  
4          NaN       NaN        NaN

In [192]:
#How many coordinates do we have for each artist credit in this third merge?
df4.notnull().sum(axis=0)

credit_id           1556313
artist_id           1556313
artist_mbid         1556313
start_area1          695378
start_area2           34527
artist_name         1556313
area_name              5968
area_id                5968
subdivision_name       5968
country_name           5968
latitude               5968
longitude              5968
dtype: int64

Thanks to the 1 Million Songs Dataset, we have been able to retrieve the origin for 5968 artist credits.

We'll save it in retrieved_credit4 and see what's pending:

In [193]:
retrieved_credit4 = df4[df4['country_name'].notnull()]

In [194]:
pending_credit4 = df4[df4['country_name'].isnull()]
#drop empty columns:
to_drop = ['area_id', 'subdivision_name','area_name', 'country_name', 'latitude', 'longitude']
pending_credit4.drop(labels=to_drop, axis=1, inplace=True)

In [195]:
#How many artists do we have without origin information?
pending_credit4['artist_id'].nunique()

808652

We can now merge all our retrieved_credit dataframes into 1 and start merging that information into the releases:

In [196]:
#Changing columns names for the first one:
retrieved_credit1.rename(columns={'area_name_x':'area_name'}, inplace=True)
#Dropping useless columns:
to_drop = ['start_area1', 'start_area2', 'code_type', 'area_name_y', 'area_id']
retrieved_credit1.drop(labels=to_drop, axis=1, inplace=True)

In [197]:
#Changing columns names for the second one:
retrieved_credit2.rename(columns={'area_name_x':'area_name', \
                                 'subdivision_name_y': 'subdivision_name'}, inplace=True)
#Dropping useless columns:
to_drop = ['start_area1', 'start_area2', 'code_type', 'area_name_y', 'subdivision_name_x', 'area_id']
retrieved_credit2.drop(labels=to_drop, axis=1, inplace=True)

In [198]:
#Dropping useless columns for the third one:
to_drop = ['start_area1', 'start_area2']
retrieved_credit3.drop(labels=to_drop, axis=1, inplace=True)

In [199]:
retrieved_credit3.columns

Index(['credit_id', 'artist_id', 'artist_mbid', 'artist_name', 'latitude',
       'longitude', 'area_name', 'subdivision_name', 'country_name'],
      dtype='object')

In [200]:
#Dropping useless columns for the fourth one:
to_drop = ['start_area1', 'start_area2', 'area_id']
retrieved_credit4.drop(labels=to_drop, axis=1, inplace=True)

In [202]:
all_credits_retrieved = pd.concat([retrieved_credit1, retrieved_credit2,\
                                   retrieved_credit3, retrieved_credit4], ignore_index=True)
all_credits_retrieved.head()

area_name  artist_id                           artist_mbid  \
0  Kingston upon Hull    1075202  d8d9139a-51b9-4983-bbaa-4853a1485c94   
1         Netherlands     471271  ff1072ec-8c36-4b01-879b-47166cab1536   
2             Ventnor     295560  16fec377-b791-4443-9e44-269ddcd9e299   
3              London     180899  9f0b3f9d-72b8-49b3-8b1b-5a0ec3b7c577   
4              Dundee    1171183  955861e9-9822-402d-94c0-52ab31ed42ed   

      artist_name                country_name  credit_id   latitude  \
0  Delfino Square              United Kingdom    1258383  52.355518   
1     Duo de Munk  Kingdom of the Netherlands     471271  52.132633   
2    Death Throes              United Kingdom     295560  52.355518   
3         Cmetric              United Kingdom     180899  52.355518   
4   The Shithawks              United Kingdom    1389970  56.490671   

   longitude subdivision_name  
0  -1.174320          England  
1   5.291266      Netherlands  
2  -1.174320          England  
3  -1.174320          England  
4  -4.202646         Scotland

In [203]:
all_credits_retrieved['artist_id'].nunique()

206532

## <font color=blue>2) Release information</font>

### Data from Musicbrainz.org

The objective of this project is to visualize when each artist released for the first time a certain CD/Album/Single etc. So, we will use Musicbrainz's release & release group to get that information.

If we look at the "releases" table:

In [204]:
releases = pd.read_csv('Data_in/Musicbrainz/release.txt',\
                       sep='\t', header=None, engine='c', usecols=[0,2,3,4])
releases.columns = ['release_id','release_group','credit_id','group_id']
releases.head()

release_id           release_group  credit_id  group_id
0           9       A Sorta Fairytale         60    896742
1          10       A Sorta Fairytale         60    896742
2          11       Glory of the 80's         60     95360
3          12  Silent All These Years         60    104189
4          26                  Demons      20211     94299

We can see, in the first 2 rows, that the same CD/Album can be released/remastered many times. According to Musicbrainz's field description for each release (https://musicbrainz.org/doc/Release):

"A MusicBrainz release represents the unique release (i.e. issuing) of a product on a specific date with specific release information such as the country, label, barcode and packaging. If you walk into a store and purchase an album or single, they are each represented in MusicBrainz as one release".

If we look at another release-related field in Musicbrainz, we find the "release group" (https://musicbrainz.org/doc/Release_Group):

"A release group, just as the name suggests, is used to group several different releases into a single logical entity. Every release belongs to one, and only one release group.

Both release groups and releases are "albums" in a general sense, but with an important difference: a release is something you can buy as media such as a CD or a vinyl record, while a release group embraces the overall concept of an album -- it doesn't matter how many CDs or editions/versions it had."

By reading these descriptions, we can clearly see that the release group is the table we are looking for as it represents a single creation, no matter how many times it has been edited or released afterwards. So we will have to keep the first release id for each release group.

In [205]:
release_year = pd.read_csv('Data_in/Musicbrainz/release_country.txt',\
                           sep='\t', header=None, engine='c', usecols=[0,2])
release_year.columns = ['release_id','release_year']
release_year.head()

release_id  release_year
0           3        1997.0
1     1427792        2014.0
2           9        2002.0
3          10        2002.0
4          11        1999.0

In [206]:
df5 = pd.merge(releases, release_year, how='left', on='release_id')
df5.head()

release_id           release_group  credit_id  group_id  release_year
0           9       A Sorta Fairytale         60    896742        2002.0
1          10       A Sorta Fairytale         60    896742        2002.0
2          11       Glory of the 80's         60     95360        1999.0
3          12  Silent All These Years         60    104189        1997.0
4          26                  Demons      20211     94299        1998.0

In [207]:
#Let's see how many releases we have:
df5['release_id'].nunique()

2198457

In [208]:
df5.isnull().sum(axis=0)

release_id            0
release_group         7
credit_id             0
group_id              0
release_year     341983
dtype: int64

In [209]:
#We want to keep only the releases which have a release year, so we can drop the others:
df5.dropna(subset=['release_year'], axis=0, inplace=True)
df5['release_year'] = df5.release_year.astype(int,inplace=True)
df5['release_id'].nunique()

1859982

In [210]:
#Let's analyze the year column:
pd.options.display.max_rows = 2000
df5.groupby('release_year').count()

release_id  release_group  credit_id  group_id
release_year                                                
1                      2              2          2         2
4                      1              1          1         1
5                      5              5          5         5
7                      1              1          1         1
8                      2              2          2         2
10                     3              3          3         3
14                     1              1          1         1
17                     4              4          4         4
18                     1              1          1         1
19                     3              3          3         3
20                     2              2          2         2
21                     1              1          1         1
23                     1              1          1         1
24                     1              1          1         1
25                     2              2          2         2
28                     2              2          2         2
29                     2              2          2         2
31                     2              2          2         2
73                     1              1          1         1
195                    1              1          1         1
198                    1              1          1         1
199                    2              2          2         2
200                    4              4          4         4
201                    4              4          4         4
209                    2              2          2         2
666                    1              1          1         1
701                    1              1          1         1
996                    1              1          1         1
1009                   1              1          1         1
1029                   1              1          1         1
1198                   1              1          1         1
1694                   1              1          1         1
1886                   1              1          1         1
1889                   1              1          1         1
1890                 249            249        249       249
1891                  11             11         11        11
1892                 130            130        130       130
1893                 183            183        183       183
1894                  29             29         29        29
1895                   2              2          2         2
1896                   6              6          6         6
1897                  65             65         65        65
1898                 183            183        183       183
1899                 281            281        281       281
1900                 131            131        131       131
1901                 199            199        199       199
1902                 234            234        234       234
1903                 196            196        196       196
1904                 155            155        155       155
1905                 163            163        163       163
1906                 154            154        154       154
1907                 171            171        171       171
1908                 212            212        212       212
1909                 187            187        187       187
1910                 115            115        115       115
1911                  54             54         54        54
1912                  37             37         37        37
1913                  13             13         13        13
1914                  22             22         22        22
1915                  12             12         12        12
1916                  26             26         26        26
1917                 135            135        135       135
1918                  87             87         87        87
1919                  46             46         4

In [213]:
#Which are the old releases?
df5[df5['release_year']<1890].head(20)

release_id                      release_group  credit_id  group_id  \
132016      2166840                        Premonition    2208600   1964778   
456904      2355726                     Yellow Islands    1346324   2113482   
461026      2131956                               LaZy    1694813   1936498   
596235      2098293                     Shining Knight    2141471   1910249   
660843      2358509                     Winner & Loser    2373882   2115818   
882916      2144976       The Good Guys Orchestra Live    2184897   1946846   
1266574      386698                          Whistling     523308    712439   
1628664     1829701                             R.E.D.    1253368   1700614   
1659620     1854547                       Super Eagles    1744202   1720039   
1682621     2375955                   I Satans Fotspor    2389088   2130391   
1688778     1996106  Secretos del Bosque De Los Sueños    2031454   1829514   
1691799     1869019                   Pleasure Complex     363160   1731159   
1721501     1882308                         No Brainer    1822886   1741173   
1725162     1883932             Gangman Into The Light    1829243   1742387   
1730582     1886379                               3016    1583812   1744266   
1730607     1886385                           About 77    1583812   1744272   
1735597     1884561                    Rite of Passage    1830733   1742865   
1776028     1011546                     Temps de Crise     258561    409827   
1778717     1912590                          Djalminha    1934561   1764347   
1807021     1929618                      Still In Love    1350711   1777860   

         release_year  
132016              1  
456904             19  
461026              5  
596235             25  
660843            198  
882916            200  
1266574          1889  
1628664             5  
1659620             8  
1682621           666  
1688778            17  
1691799            31  
1721501            29  
1725162            20  
1730582            19  
1730607            29  
1735597            10  
1776028           201  
1778717            14  
1807021            10

By looking at the different year values, we can see that the year could have been incorrectly informed for some rows.

In order to avoid incorrect data and to have enough values per year, we could drop the rows whose year is below 1890 and above 2019. Our visualization would have 130 years, which is pretty good.

In [214]:
df5.drop(df5[df5['release_year'] < 1890].index , inplace=True)
df5.drop(df5[df5['release_year'] >2019].index , inplace=True)
df5.sort_values(by=['release_year']).head()

release_id                  release_group  credit_id  group_id  \
1266766      386919      Visions of Paradise Waltz      97546    712605   
1266956      386830  German Ballad with Variations      97546    712514   
1266958      386829  German Ballad with Variations      97546    712514   
1266960      386828           Mountain Bells Polka      97546    712513   
1266961      386827           Mountain Bells Polka      97546    712513   

         release_year  
1266766          1890  
1266956          1890  
1266958          1890  
1266960          1890  
1266961          1890

In [215]:
#Converting the year column to datetime for later:
df5['release_year'] = pd.to_datetime(df5['release_year'].astype(str), format='%Y')
df5.dtypes

release_id                int64
release_group            object
credit_id                 int64
group_id                  int64
release_year     datetime64[ns]
dtype: object

In [216]:
#We sort by release id and year (we could have 2 release groups with the same name but produced by different artists):
df5.sort_values(['release_group','release_year','credit_id'], ascending=[True,True,True], inplace=True)
df5.head()

release_id            release_group  credit_id  group_id release_year
2026273     2163750                             2205562   1962329   2014-01-01
1648516     1846605                             1503027   1713833   2015-01-01
1250325     1714060    Beaux Soirs De Paris     1324142   1609358   1995-01-01
2116340     2265346                    Le 1     2291833   2042812   2018-01-01
1748061     1895266   M2Music HitDisc Vol. 1          1   1751021   2006-01-01

In [217]:
df5[df5['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  group_id release_year
1836724     2378622    Artaxerxes    2392005   2132682   1996-01-01
1910376     2379252    Artaxerxes    2392005   2132682   2009-01-01
1909444     2379244    Artaxerxes    2392011   2133192   2011-01-01

In [218]:
#Now we can delete the duplicate release group and keep the ones who were first released:
df5.drop_duplicates(subset=['release_group'],keep='first', inplace=True)
df5['release_id'].nunique()

1207453

In [219]:
#Just to double-check:
df5[df5['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  group_id release_year
1836724     2378622    Artaxerxes    2392005   2132682   1996-01-01

## <font color=blue>3) Matching releases with artists</font>

Now that we have both artist and releases dataframes, we can join them, knowing that, for all the releases whose credit belongs to more than one artist, will appear as many times as the number of artists in the credit.

As we don't want to show duplicate releases, we need to keep only one artist per release. We will keep the first artist appearing for each release.

In [220]:
#We first merge with the artists_credits dataframe, to retrieve all the artists names:
df6 = pd.merge(df5, artists_credit, how='left', on='credit_id')
df6.head()

release_id            release_group  credit_id  group_id release_year  \
0     2163750                             2205562   1962329   2014-01-01   
1     1714060    Beaux Soirs De Paris     1324142   1609358   1995-01-01   
2     2265346                    Le 1     2291833   2042812   2018-01-01   
3     1895266   M2Music HitDisc Vol. 1          1   1751021   2006-01-01   
4     1772538             devil jokes     1653884   1656147   2016-01-01   

   artist_id      artist_name  
0  1654312.0         Soul Glo  
1  1122795.0  Soixante Étages  
2  1720981.0         TedeuzeM  
3        1.0  Various Artists  
4  1363025.0            yzome

In [221]:
#And now we merge with all_credits_retrieved to retrieve the artists for which we have coordinates:
df7 = pd.merge(df6, all_credits_retrieved, how='left', on='credit_id')
df7.head()

release_id            release_group  credit_id  group_id release_year  \
0     2163750                             2205562   1962329   2014-01-01   
1     1714060    Beaux Soirs De Paris     1324142   1609358   1995-01-01   
2     2265346                    Le 1     2291833   2042812   2018-01-01   
3     1895266   M2Music HitDisc Vol. 1          1   1751021   2006-01-01   
4     1772538             devil jokes     1653884   1656147   2016-01-01   

   artist_id_x    artist_name_x        area_name  artist_id_y  \
0    1654312.0         Soul Glo     Philadelphia    1654312.0   
1    1122795.0  Soixante Étages              NaN          NaN   
2    1720981.0         TedeuzeM  Aix-en-Provence    1720981.0   
3          1.0  Various Artists              NaN          NaN   
4    1363025.0            yzome          Seattle    1363025.0   

                            artist_mbid artist_name_y   country_name  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a      Soul Glo  United States   
1                                   NaN           NaN            NaN   
2  a69efb5f-0b28-4328-8ff0-44d8d6f39755      TedeuzeM         France   
3                                   NaN           NaN            NaN   
4  c941ad72-8b13-4940-8d99-0ed9becad2d7         yzome  United States   

    latitude   longitude            subdivision_name  
0  41.203322  -77.194525                Pennsylvania  
1        NaN         NaN                         NaN  
2  43.935169    6.067919  Provence-Alpes-Côte-d'Azur  
3        NaN         NaN                         NaN  
4  47.751074 -120.740139                  Washington

In [222]:
len(df7)

1713339

In [223]:
#As we did two merges by credit, there are duplicate entries now:
df7.sort_values(by=['release_id','latitude'], inplace=True)
df7.drop_duplicates(subset='release_id', keep='first', inplace=True)
len(df7)

1207453

In [224]:
df7.isnull().sum(axis=0)

release_id               0
release_group            1
credit_id                0
group_id                 0
release_year             0
artist_id_x            124
artist_name_x          127
area_name           612516
artist_id_y         612516
artist_mbid         612516
artist_name_y       612516
country_name        612516
latitude            612516
longitude           612516
subdivision_name    612516
dtype: int64

What kind of artists do we have in our dataframe? Which artists produced the most releases?

In [225]:
df7.groupby('artist_name_x').count().sort_values('release_id',ascending=False).head(100)

release_id  release_group  credit_id  \
artist_name_x                                                          
Various Artists                     128419         128419     128419   
Johann Sebastian Bach                 1653           1653       1653   
[unknown]                             1223           1223       1223   
Mozart                                1148           1148       1148   
Wolfgang Amadeus Mozart               1117           1117       1117   
Bruce Springsteen                     1099           1099       1099   
Beethoven                             1051           1051       1051   
Ludwig van Beethoven                   971            971        971   
Phish                                  622            622        622   
Pearl Jam                              566            566        566   
Ennio Morricone                        542            542        542   
Franz Schubert                         535            535        535   
Elvis Presley                          515            515        515   
Tangerine Dream                        483            483        483   
Tchaikovsky                            482            482        482   
Antonio Vivaldi                        481            481        481   
The Rolling Stones                     469            469        469   
The Beatles                            457            457        457   
Brahms                                 439            439        439   
Metallica                              402            402        402   
Joseph Haydn                           400            400        400   
Bach                                   395            395        395   
Frank Sinatra                          390            390        390   
Johannes Brahms                        378            378        378   
Merzbow                                363            363        363   
Louis Armstrong                        353            353        353   
Dvořák                                 350            350        350   
Ella Fitzgerald                        343            343        343   
Depeche Mode                           326            326        326   
Bob Dylan                              315            315        315   
John Williams                          313            313        313   
Miles Davis                            309            309        309   
Schubert                               306            306        306   
Johnny Cash                            300            300        300   
KISS                                   298            298        298   
Buckethead                             289            289        289   
Vivaldi                                287            287        287   
Chopin                                 287            287        287   
Shostakovich                           287            287        287   
David Bowie                            284            284        284   
Jean Sibelius                          279            279        279   
Frédéric Chopin                        269            269        269   
The Cherry Blues Project               267            267        267   
Debussy                                265            265        265   
Antonín Dvořák                         263            263        263   
Franz Liszt                            257            257        257   
Sibelius                               254            254        254   
Grateful Dead                          252            252        252   
The Beach Boys                         248            248        248   
Vitamin String Quartet                 248            248        248   
Haydn                                  247            247        247   
Die drei ???                           244            244        244   
Richard Strauss                        243            243        243   
Pink Floyd                             241            241        241   


In [226]:
#From what we can see above, the category "Various Artists" has many releases assigned:
df7[df7['artist_name_x']=='Various Artists']

release_id                                      release_group  \
943450           80                    Now That's What I Call Music! 4   
122299          111                    Atlantic Jazz: Best of the '70s   
270378          113                           Classic FM: Hall of Fame   
666071          135                        It’s a Cool, Cool Christmas   
966206          253   One Way: A Showcase for New Music (Dec/Jan 2003)   
86697           407      Alligator Records 30th Anniversary Collection   
1327548         410  The Alligator Records 20th Anniversary Collection   
1328294         456                                    The Annual 2004   
943656          551                   Now That’s What I Call Music! 56   
225088          613     CMJ New Music Monthly, Volume 50: October 1997   
225093          614       CMJ New Music Monthly, Volume 55: March 1998   
225105          615    CMJ New Music Monthly, Volume 66: February 1999   
225081          616       CMJ New Music Monthly, Volume 43: March 1997   
225117          617     CMJ New Music Monthly, Volume 77: January 2000   
225135          618         CMJ New Music Monthly, Volume 93: May 2001   
1055814         629      Punk-O-Rama, Volume 4: Straight Outta the Pit   
1326490         670      The Acid House: Music From the Motion Picture   
940001          673  Not Another Teen Movie: Music From the Motion ...   
1057055         677                            Pure Urban Essentials 2   
606498          685                                     Huge Hits 2004   
1328338         791                            The Annual: Spring 2003   
1582494         793                                  WoW 1996 (disc 2)   
1473910         794                              Trance Nation: Deeper   
904785          797                          My Utmost for His Highest   
535129          801  God With Us: A Celebration of Christmas Carols...   
1333843         806                         The Best Club Anthems 2003   
1207143         807                       Songs 4 Worship: Holy Ground   
1207130         809                      Songs 4 Life: Feel the Power!   
412005          831                               Earth Girls Are Easy   
1473789         955                            Trance Europe Express 3   
1544828         969                                           WOW 1998   
1544838         970                                           WOW Gold   
591255          974  History Makers: The Best of Praise and Worship...   
577378         1002                              Heavy Righteous Metal   
1330864        1003                                         The Axemen   
54609          1005          A Steve Taylor Tribute: I Predict a Clone   
577379         1008                 Heavy Righteous Metal - Chapter II   
1118482        1009                                        Rugged Cuts   
329188         1087                               Daredevil: The Album   
498806         1090                                   Freddy vs. Jason   
908991         1108                                NASCAR: Crank It Up   
498809         1116                 Freddy's Dead: The Final Nightmare   
1431905        1118                          The Ultimate Cheese Party   
592484         1119                                            Hits 56   
943655         1121                   Now That’s What I Call Music! 55   
1035477        1122                                          Pop Party   
51631          1143                                 A Perfect Love III   
276357         1149                 Clubland 4: The Night of Your Life   
276369         1150              Clubland III: The Sound of the Summer   
276434         1151                                Clubmix Summer 2003   
310466         1152                          Cream Trance Anthems 2003   
325400         1153                               Dance Nation Anthems   
1431909        1173                The Ultimate Chick Flick Soundtrack   
1229909      

If we look in detail into these releases, we can see that most of them are music compilations (hence the generic category "Various Artists"). As they are music compilations, that means that the tracks included were originally released before by their genuine author, so we shouldn't take them into account. Also, as we don't have an artist name for them, it will be impossible to retrieve the origin.

We will delete those rows from our dataframe later.

Let's analyze more in detail who are the rest of artists that have many releases, and decide what to do with them.

In [227]:
#"Language instruction" artist:
df7[df7['artist_name_x']=='[language instruction]']

release_id                                      release_group  \
1219842      179513                         Spanish: Beyond the Basics   
1368133      196550                            The French Experience 1   
1497989      253239       Ultimate Spanish: Beginner-Intermediate (A2)   
1497988      253241       Ultimate Spanish: Beginner-Intermediate (A1)   
1497990      253246       Ultimate Spanish: Beginner-Intermediate (A3)   
1497991      253248       Ultimate Spanish: Beginner-Intermediate (A4)   
1497992      253255       Ultimate Spanish: Beginner-Intermediate (B1)   
1497993      253269       Ultimate Spanish: Beginner-Intermediate (B2)   
1497994      253277       Ultimate Spanish: Beginner-Intermediate (B3)   
1497995      253282       Ultimate Spanish: Beginner-Intermediate (B4)   
645073       259244                                  In-Flight Chinese   
498035       283506  Französisch kompakt: Ein Selbstlernkurs für An...   
197284       361228         Bonne Route! Students' Listening Exercises   
407656       376354                              Découvertes, Volume 1   
662683       394985                            Italienisch in 30 Tagen   
1471119      398409                  Tous ensemble, Volume 1 : Schüler   
1121969      399434                        Réalités 2 nouvelle édition   
1121968      399716                        Réalités 1 nouvelle édition   
466664       402551              Fast and Easy: Basic English Course 1   
407657       403893                              Découvertes, Volume 2   
1471120      404821                  Tous ensemble, Volume 2 : Schüler   
650809       409803                         Instant Immersion: Italian   
662052       436837                          Italian Beginner (disc 1)   
138489       475724                       Baby's First Words in French   
138490       478425                      Baby's First Words in Italian   
520971       502359  Genki I: An Integrated Course in Elementary Ja...   
606679       519749                Hugo in 3 Months - Italian (disc 1)   
520972       557483  Genki II: An Integrated Course in Elementary J...   
1041351      586794     Praktischer Sprachlehrgang Russisch: Dialoge 1   
1041352      586810  Praktischer Sprachlehrgang Russisch: Hör- und ...   
754435       656961                            Learn Italian in a Week   
754434       657068                                      Learn Italian   
355331       677095          Der neue Hörkurs: Französisch ganz leicht   
85334        685879                                  All-Audio Spanish   
419743       688016                               Einstieg tschechisch   
871674       707899                          Modernes Russisch: OKNO 1   
1615866      715365                      inlingua Deutsch 1 Hörübungen   
870671       717380                Mobil Wortschatztraining Schwedisch   
672183       731207                               Japanese for Dummies   
1443422      731366                      Themen aktuell 2, Lektion 1-5   
1615867      745866                      inlingua Deutsch 2 Hörübungen   
672181       788466  Japanese for Busy People III - The Workbook fo...   
359116       798635            Deutsch in 30 Tagen – German in 30 Days   
1620813      804513                            studio d A2, Teilband 1   
12123        821781                                   15 Minute French   
12124        822699                                  15 Minute Italian   
397708       825118                                  Drive Time French   
1620814      828398                            studio d A2, Teilband 2   
408635       853354                                       E nagu Eesti   
1613236     1064876               em neu 2008 Brückenkurs, Lektion 1-5   
1613237     1073309              em neu 2008 Brückenkurs, Lektion 6-10   
435886      1099755                            Englisch Großer Hörkurs   
397709      1107637                  Drive Time German: Beginner Level   
1231642     1

As its name suggests, these releases are language courses recorded, so they are not music and they are out of our scope too.

The same would apply to the categories [unknown],[nature sounds], [dialogue], [christmas music], [no artist] and [church chimes].

We can now delete from our dataframes all these cathegories, and see what we have left.

In [228]:
#In our main dataframe:
labels = ['[unknown]','[nature sounds]','[dialogue]','[christmas music]',\
          '[no artist]', '[church chimes]','Various Artists','[language instruction]']
df7.drop(df7[df7['artist_name_x'].isin(labels)].index, axis=0, inplace=True)

In [229]:
len(df7)

1077168

In [237]:
#Wich are the unknow artists that produce the most releases?
unknown_artists = df7[df7['country_name'].isnull()].groupby(by='artist_name_x', axis=0).count()
unknown_artists.sort_values(by='release_id',axis=0, ascending=False)

release_id  release_group  \
artist_name_x                                                                   
The Cherry Blues Project                                   267            267   
Vitamin String Quartet                                     248            248   
Die drei ???                                               244            244   
Senmuth                                                    231            231   
Stefan Wolf                                                213            213   
Glee Cast                                                  200            200   
モーニング娘。                                                    200            200   
Duke Ellington & His Orchestra                             183            183   
Dwelling of Duels                                          180            180   
Enid Blyton                                                164            164   
TAMUSIC                                                    139            139   
Pritam                                                     126            126   
Benny Goodman and His Orchestra                            126            126   
Falcom Sound Team jdk                                      123            123   
Léo Ferré                                                  120            120   
Peerless Orchestra                                         118            118   
THE ALFEE                                                  116            116   
Michel Sardou                                              113            113   
Bibi & Tina                                                109            109   
Ajda Pekkan                                                108            108   
Dan Gibson                                                 106            106   
Edison Concert Band                                        103            103   
Grupo Niche                                                101            101   
ZUNTATA                                                    100            100   
How Did This Get Made?                                      98             98   
Berryz工房                                                    98             98   
Аквариум                                                    98             98   
Kevin Drumm                                                 98             98   
보천보전자악단                                                     97             97   
Edward M. Favor                                             96             96   
Jonathan Parecki                                            96             96   
コナミ矩形波倶楽部                                                   96             96   
桜庭統                                                         95             95   
Samuel Sagan                                                95             95   
三遊亭圓生                                                       94             94   
℃‐ute                                                       89             89   
[Disney]                                                    89             89   
Tim Pritlove                                                89             89   
ALI PROJECT                                                 88             88   
B’z                                                         85             85   
SMAP                                                        85             85   
Every Little Thing                                          84             84   
Miracle of Sound                                            83             83   
Loudness                                                    83             83   
Laxmikant Pyarelal                                          83             83   
HasenChat Music                                             83             83   
サザンオールスターズ                                                  81             81   
John Sinclair                                               81             81   
Da

If we search online for the second artist, "Vitamin String Quartet", we can find a Wikipedia page with the information we need about the musical group's origin. This happens with many other artists for which we haven't still been able to retrieve their detailed origin.

What we'll do in step 4 is to search for all of them in Wikipedia and gather their origins in a dataframe.

In [239]:
#How many releases do we have identified for now?
origin_retrieved = df7[df7['latitude'].notnull()]
len(origin_retrieved)

593528

In [241]:
#First, we tidy up our columns:
origin_retrieved.rename(columns={'artist_id_y':'artist_id','artist_name_y':'artist_name'}, inplace=True)

In [244]:
#We drop the unnecessary ones:
to_drop = ['artist_id_x', 'artist_name_x']
origin_retrieved.drop(labels=to_drop, axis=1, inplace=True)

In [247]:
#And how much do we have pending?
unknown_origin = df7[df7['latitude'].isnull()]
len(unknown_origin)

483640

In [254]:
unknown_origin.isnull().sum(axis=0)

release_id         0
release_group      0
credit_id          0
group_id           0
release_year       0
artist_id_x      124
artist_name_x    125
dtype: int64

In [249]:
#We drop the unnecessary columns:
columns = ['area_name','subdivision_name', 'country_name', \
           'latitude', 'longitude', 'artist_id_y', 'artist_name_y', 'artist_mbid']
unknown_origin.drop(labels=columns, axis=1, inplace=True)

In [255]:
#We rename the columns for artists:
unknown_origin.rename(columns={'artist_id_x':'artist_id', \
                              'artist_name_x': 'artist_name'}, inplace=True)

In [256]:
#We'll export the file and search for the origin in the notebook "Wikipedia artist information retrieval:"
unknown_origin.to_csv('Data_out/unknown_artist_origin_2.csv', sep='\t', index=False, encoding='utf-8')

## <font color=blue>4) Retrieving extra information from Wikipedia</font>

In [257]:
#Importing the file with the information retrieved:
wikipedia = pd.read_csv('Data_out/Wikipedia_retrieved_origins.csv', sep='\t', header=0, encoding='utf-8')
wikipedia.head()

area_id area_name  artist_id   country_name   latitude   longitude  \
0    266.0       NaN   562672.0  United States  36.778261 -119.417932   
1    276.0       NaN   119635.0  United States  40.633125  -89.398528   
2    295.0       NaN   523680.0  United States  40.712775  -74.005973   
3    292.0       NaN  1037860.0  United States  40.058324  -74.405661   
4    266.0       NaN    11108.0  United States  36.778261 -119.417932   

  subdivision_name  
0       California  
1         Illinois  
2         New York  
3       New Jersey  
4       California

In [258]:
#We can now merge our unknown origin dataframe with this new one:
origin_wikipedia = pd.merge(unknown_origin, wikipedia, how='left', on='artist_id')
origin_wikipedia.head()

release_id            release_group  credit_id  group_id release_year  \
0          68  What I Go to School For      59115    737994   2002-01-01   
1          71       Year 3000 (disc 2)      59115    101019   2003-01-01   
2          72       Year 3000 (disc 1)      59115    101019   2003-01-01   
3          73              You Said No      59115    124527   2003-01-01   
4         145               Sacred Sky     118094    173547   2002-01-01   

   artist_id                     artist_name  area_id area_name country_name  \
0    59115.0                          Busted      NaN       NaN          NaN   
1    59115.0                          Busted      NaN       NaN          NaN   
2    59115.0                          Busted      NaN       NaN          NaN   
3    59115.0                          Busted      NaN       NaN          NaN   
4   118094.0  Genie Nilsson and Troy Nilsson      NaN       NaN          NaN   

   latitude  longitude subdivision_name  
0       NaN        NaN              NaN  
1       NaN        NaN              NaN  
2       NaN        NaN              NaN  
3       NaN        NaN              NaN  
4       NaN        NaN              NaN

In [259]:
len(origin_wikipedia)

483640

In [260]:
#And drop the null values by coordinates:
origin_wikipedia.dropna(subset=['latitude'], axis=0, inplace=True)

In [261]:
#For how many releases did we retrieve the origin for in this last step?
len(origin_wikipedia)

51451

In [262]:
#We can now unify both dataframes into the final one:
final = pd.concat([origin_retrieved, origin_wikipedia], ignore_index=True)

In [264]:
len(final)

644979

In [265]:
#We sort by release group and date and we keep the first ones released:
final.sort_values(by=['group_id', 'release_year'],inplace=True)
#And we remove the duplicate group_id's:
final.drop_duplicates(subset='group_id', inplace=True)

In [266]:
len(final)

617096

In [267]:
#Ordering the columns for better visibility:
order = ['release_id','release_group', 'group_id','release_year',\
         'artist_id','artist_mbid', 'credit_id','artist_name',\
         'area_id', 'area_name','subdivision_name','country_name', 'latitude', 'longitude']
final_export = final.reindex(columns=order)

Now that we have retrieved the maximum detail regarding the releases' origin, we can skip to the next step: identifying the musical genre of each release. This will be done in the following notebook: "Data_ganthering_music_genre_in_detail".

In [268]:
final_export.to_csv('Data_out/Dataframe_with_origin_2.csv', sep='\t', index=False, encoding='utf-8')